In [15]:
## import statements
from langchain_community.document_loaders import PyPDFLoader
from langchain_text_splitters import RecursiveCharacterTextSplitter
import os
from dotenv import load_dotenv
load_dotenv()
from langchain_chroma import Chroma

In [3]:
#loading data
loader=PyPDFLoader(r"C:\Users\harsu\OneDrive\ANESTH~1\STOELT~1.PDF")
docs=loader.load()
docs

[Document(metadata={'producer': 'Adobe Acrobat 8.0 Image Conversion Plug-in', 'creator': 'Adobe Acrobat 8.0 Combine Files', 'creationdate': '2012-09-21T09:57:37+07:00', 'moddate': '2012-11-11T08:14:27-05:00', 'source': 'C:\\Users\\harsu\\OneDrive\\ANESTH~1\\STOELT~1.PDF', 'total_pages': 683, 'page': 0, 'page_label': '1'}, page_content=''),
 Document(metadata={'producer': 'Adobe Acrobat 8.0 Image Conversion Plug-in', 'creator': 'Adobe Acrobat 8.0 Combine Files', 'creationdate': '2012-09-21T09:57:37+07:00', 'moddate': '2012-11-11T08:14:27-05:00', 'source': 'C:\\Users\\harsu\\OneDrive\\ANESTH~1\\STOELT~1.PDF', 'total_pages': 683, 'page': 1, 'page_label': '2'}, page_content="1600 John F. Kennedy Blvd.\nSte 1800\nPhiladelphia, PA 19103-2899\nSTOELTING'S ANESTHESIA AND CO-EXISTING DISEASE ISBN: 978-1-4557-0082-0\nCopyright © 2012 by Saunders, an imprint of Elsevier Inc.\nNo part of this publication may be reproduced or transmitted in any form or by any means, electronic or mechani-\ncal, inc

In [5]:
text_splitter=RecursiveCharacterTextSplitter(chunk_size=1000,chunk_overlap=50)
chunks=text_splitter.split_documents(docs)
chunks

[Document(metadata={'producer': 'Adobe Acrobat 8.0 Image Conversion Plug-in', 'creator': 'Adobe Acrobat 8.0 Combine Files', 'creationdate': '2012-09-21T09:57:37+07:00', 'moddate': '2012-11-11T08:14:27-05:00', 'source': 'C:\\Users\\harsu\\OneDrive\\ANESTH~1\\STOELT~1.PDF', 'total_pages': 683, 'page': 1, 'page_label': '2'}, page_content="1600 John F. Kennedy Blvd.\nSte 1800\nPhiladelphia, PA 19103-2899\nSTOELTING'S ANESTHESIA AND CO-EXISTING DISEASE ISBN: 978-1-4557-0082-0\nCopyright © 2012 by Saunders, an imprint of Elsevier Inc.\nNo part of this publication may be reproduced or transmitted in any form or by any means, electronic or mechani-\ncal, including photocopying, recording, or any information storage and retrieval system, without permission in \nwriting from the Publisher. Details on how to seek permission, further information about the Publisher's permis-\nsions policies and our arrangements with organizations such as the Copyright Clearance Center and the Copyright \nLicensing

## Creating Embeddings

In [6]:
os.environ['HF_TOKEN']=os.getenv("HF_TOKEN")

In [7]:
from langchain_huggingface import HuggingFaceEmbeddings
embeddings=HuggingFaceEmbeddings(model_name="all-MiniLM-L6-v2")

## Create VectorDB

In [8]:
vectordb=Chroma.from_documents(documents=chunks,embedding=embeddings)
vectordb

In [10]:
## Saving to the disk
vectordb=Chroma.from_documents(documents=chunks,embedding=embeddings,persist_directory="./chroma_db")


In [13]:
## query it
query = "when does cardic transplantation is conducted on a patient?"
docs = vectordb.similarity_search(query)
docs

[Document(id='093cdc72-de05-4186-b8ad-023156d9652c', metadata={'moddate': '2012-11-11T08:14:27-05:00', 'creator': 'Adobe Acrobat 8.0 Combine Files', 'creationdate': '2012-09-21T09:57:37+07:00', 'producer': 'Adobe Acrobat 8.0 Image Conversion Plug-in', 'total_pages': 683, 'page_label': '219', 'source': 'C:\\Users\\harsu\\OneDrive\\ANESTH~1\\STOELT~1.PDF', 'page': 218}, page_content='cation to transplantation because of the risk of cancer recur -\nrence with immunosuppression.) Mild to moderate degrees of \npulmonary hypertension and some degree of right-sided heart \nfailure are often present. Smokers should have quit smoking \nat least 6 to 12 months before transplantation. The ability of \nthe right ventricle to maintain an adequate stroke volume in \nthe presence of the acute increase in pulmonary vascular resis-\ntance produced by clamping the pulmonary artery before the \nnative lung is removed needs to be assessed. Evaluation of oxy-\ngen dependence and steroid use, hematologic an

## Create Chains

In [16]:
os.environ["GROQ_API_KEY"]=os.getenv("GROQ_API_KEY")

In [18]:
from langchain_groq import ChatGroq

llm=ChatGroq(model="llama-3.1-8b-instant")
llm.invoke("Hey I am Harry and i am MscAC student")

AIMessage(content="Nice to meet you, Harry. You're an MSc in Accounting (AC) student, right? That's a great field of study. How's your experience so far in the program? Are you enjoying it?", additional_kwargs={}, response_metadata={'token_usage': {'completion_tokens': 45, 'prompt_tokens': 46, 'total_tokens': 91, 'completion_time': 0.06845145, 'prompt_time': 0.002684291, 'queue_time': 0.241010823, 'total_time': 0.071135741}, 'model_name': 'llama-3.1-8b-instant', 'system_fingerprint': 'fp_50a6be1b6f', 'service_tier': 'on_demand', 'finish_reason': 'stop', 'logprobs': None}, id='run--5256afa3-a7c3-403d-ab97-5271e1504d2c-0', usage_metadata={'input_tokens': 46, 'output_tokens': 45, 'total_tokens': 91})

In [24]:
## Retrieval Chain, Document chain

from langchain.chains.combine_documents import create_stuff_documents_chain
from langchain_core.prompts import ChatPromptTemplate

prompt=ChatPromptTemplate.from_template(
    """
Answer the following question based only on the provided context:
question: {input}
<context>
{context}
</context>

"""
)

document_chain=create_stuff_documents_chain(llm,prompt)
document_chain

RunnableBinding(bound=RunnableBinding(bound=RunnableAssign(mapper={
  context: RunnableLambda(format_docs)
}), kwargs={}, config={'run_name': 'format_inputs'}, config_factories=[])
| ChatPromptTemplate(input_variables=['context', 'input'], input_types={}, partial_variables={}, messages=[HumanMessagePromptTemplate(prompt=PromptTemplate(input_variables=['context', 'input'], input_types={}, partial_variables={}, template='\nAnswer the following question based only on the provided context:\nquestion: {input}\n<context>\n{context}\n</context>\n\n'), additional_kwargs={})])
| ChatGroq(client=<groq.resources.chat.completions.Completions object at 0x0000024497AA1720>, async_client=<groq.resources.chat.completions.AsyncCompletions object at 0x00000244862986A0>, model_name='llama-3.1-8b-instant', model_kwargs={}, groq_api_key=SecretStr('**********'))
| StrOutputParser(), kwargs={}, config={'run_name': 'stuff_documents_chain'}, config_factories=[])

In [25]:
retriever=vectordb.as_retriever()
from langchain.chains import create_retrieval_chain
retrieval_chain=create_retrieval_chain(retriever,document_chain)
retrieval_chain

RunnableBinding(bound=RunnableAssign(mapper={
  context: RunnableBinding(bound=RunnableLambda(lambda x: x['input'])
           | VectorStoreRetriever(tags=['Chroma', 'HuggingFaceEmbeddings'], vectorstore=<langchain_chroma.vectorstores.Chroma object at 0x00000244813BAE60>, search_kwargs={}), kwargs={}, config={'run_name': 'retrieve_documents'}, config_factories=[])
})
| RunnableAssign(mapper={
    answer: RunnableBinding(bound=RunnableBinding(bound=RunnableAssign(mapper={
              context: RunnableLambda(format_docs)
            }), kwargs={}, config={'run_name': 'format_inputs'}, config_factories=[])
            | ChatPromptTemplate(input_variables=['context', 'input'], input_types={}, partial_variables={}, messages=[HumanMessagePromptTemplate(prompt=PromptTemplate(input_variables=['context', 'input'], input_types={}, partial_variables={}, template='\nAnswer the following question based only on the provided context:\nquestion: {input}\n<context>\n{context}\n</context>\n\n'), addit

In [28]:
## Get the response form the LLM
response=retrieval_chain.invoke({"input":"what Relationship of electrocardiogram (ECG) leads to areas of myocardial ischemia?"})
response['answer']

'The relationship between electrocardiogram (ECG) leads and areas of myocardial ischemia is as follows:\n\n- The V3-V5 leads reflect myocardial ischemia in the anterolateral aspect of the left ventricle, which is supplied by the left anterior descending coronary artery.\n- The II, III, and aVF leads reflect myocardial ischemia in the inferior aspect of the left ventricle, which is supplied by the right coronary artery.\n- The I and aVL leads reflect myocardial ischemia in the lateral aspect of the left ventricle, which is supplied by the circumflex coronary artery.'

In [29]:
response

{'input': 'what Relationship of electrocardiogram (ECG) leads to areas of myocardial ischemia?',
 'context': [Document(id='97c47135-80ca-4e61-a378-a6a43f7af092', metadata={'moddate': '2012-11-11T08:14:27-05:00', 'creationdate': '2012-09-21T09:57:37+07:00', 'source': 'C:\\Users\\harsu\\OneDrive\\ANESTH~1\\STOELT~1.PDF', 'page': 28, 'creator': 'Adobe Acrobat 8.0 Combine Files', 'total_pages': 683, 'producer': 'Adobe Acrobat 8.0 Image Conversion Plug-in', 'page_label': '29'}, page_content='II, V4, and V5, or else V3, V4, and V5) improves the ability to \ndetect ischemia. There is a correlation between the lead of \nthe ECG that detects myocardial ischemia and the anatomic \ndistribution of the diseased coronary artery ( Table 1-12). For \nexample, the V 5 lead (fifth intercostal space in the anterior \naxillary line) reflects myocardial ischemia in the portion of \nthe left ventricle supplied by the left anterior descending \nTABLE 1-12 n  Relationship of electrocardiogram (ECG) \nleads t